In [1]:
#my stuff
import icu_data_defs
import transformers
import utils
import features
from constants import column_names,variable_type,clinical_source
import units
import mimic
import logger

#other stuff
from sklearn.model_selection import train_test_split,cross_val_score,ShuffleSplit
from sklearn.linear_model import LinearRegression,ElasticNet
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error
from sklearn.pipeline import Pipeline
from sklearn.base import TransformerMixin,BaseEstimator,clone

#make pretty pictures
import seaborn as sns
%matplotlib inline

In [2]:
def test_train_val_split(all_ids=None,test_size=0.1,random_state=None,print_ids=False):
    from sklearn.model_selection import train_test_split
    if all_ids is None:
        all_ids = mimic.get_all_hadm_ids()
    
    validate_size = test_size/(1-test_size)
    train_size = (1-test_size)*(1-validate_size)
    #these test IDs will never be touched again. They are sacred
    train_val_ids,test_ids = train_test_split(all_ids,test_size=test_size,random_state=random_state)
    train_ids,validate_ids = train_test_split(train_val_ids,test_size=validate_size,random_state=random_state)

    if print_ids:
        print 'Train {}:'.format(int(train_size*100)), len(train_ids),'>',train_ids[:5],'...'
        print 'Validate {}:'.format(int(train_size*100)), len(validate_ids),'>',validate_ids[:5],'...'
        print 'Test {}:'.format(int(test_size*100)), len(test_ids),'>',test_ids[:5],'...'
    return train_ids,validate_ids,test_ids

# Smart joins

In [8]:
reload(utils)
reload(logger)
data_dict = icu_data_defs.data_dictionary('config/data_definitions.xlsx')
ids = mimic.get_all_hadm_ids()
components = data_dict.get_panel_defintions(12).component.unique().tolist()
components.remove(data_dict.components.HEMOGLOBIN)
paths = ['cleaned/{}'.format(c) for c in components]
path_joined = ALL
store = utils.smart_join('data/mimic_data_noindex.h5',paths,path_joined,ids[:10000])

(2017-07-06 16:15:57) Smart join: n=10000, ['cleaned/heart rate', 'cleaned/blood pressure systolic', 'cleaned/blood pressure diastolic', 'cleaned/blood pressure mean', 'cleaned/respiratory rate', 'cleaned/temperature body', 'cleaned/oxygen saturation pulse oximetry', 'cleaned/weight body', 'cleaned/output urine', 'cleaned/glasgow coma scale motor', 'cleaned/glasgow coma scale eye opening', 'cleaned/glasgow coma scale verbal', 'cleaned/normal saline', 'cleaned/lactated ringers', 'cleaned/norepinephrine', 'cleaned/vasopressin', 'cleaned/lactate']
(2017-07-06 16:15:57)>> JOINING dataframes
index>=100001 & index<=108446
(2017-07-06 16:15:57)>>>> Slice & Join: 100001 --> 108446, n=5000
(2017-07-06 16:15:57)>>>>>> cleaned/heart rate
(2017-07-06 16:15:58)<<<<<< --- (1.0s)
(2017-07-06 16:15:58)>>>>>> cleaned/blood pressure systolic
(2017-07-06 16:16:00)<<<<<< --- (2.0s)
(2017-07-06 16:16:00)>>>>>> cleaned/blood pressure diastolic
(2017-07-06 16:16:03)<<<<<< --- (3.0s)
(2017-07-06 16:16:03)>>>>

In [32]:
df_all = store['all'].set_index([column_names.ID,column_names.DATETIME])
df_all.shape

(1387786, 46)

In [33]:
df_all.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 1387786 entries, (100001, 2117-09-11 12:57:00) to (116855, 2117-12-10 08:30:00)
Data columns (total 46 columns):
(heart rate, known, qn, beats/min, 211(BPM))                   592486 non-null float64
(heart rate, known, qn, beats/min, 211(bpm))                   287643 non-null float64
(heart rate, known, qn, beats/min, 220045(bpm))                453108 non-null float64
(heart rate, unknown, qn, no_units, 1332)                      0 non-null float64
(heart rate, unknown, qn, no_units, 1341)                      0 non-null float64
(heart rate, unknown, qn, no_units, 1725)                      0 non-null float64
(blood pressure systolic, known, qn, mmHg, 220050)             192231 non-null float64
(blood pressure systolic, known, qn, mmHg, 220179)             214853 non-null float64
(blood pressure systolic, known, qn, mmHg, 224167)             104 non-null float64
(blood pressure systolic, known, qn, mmHg, 225309)             15412 non

In [7]:
for component in data_dict.get_panel_defintions(12).component.unique().tolist():
    print component
    print 'OPENING...'
    df = pd.read_hdf('data/mimic_data.h5','cleaned/{}'.format(component))
    df.reset_index('datetime',drop=False,inplace=True)
    display(df.head())
    print 'SAVING...'
    df.to_hdf('data/mimic_data_noindex.h5','cleaned/{}'.format(component),format='t')
    del df
    

lactate
OPENING...


component                datetime lactate                                   \
status                              known                          unknown   
variable_type                          qn                              nom   
units                              mmol/L                         no_units   
description                          1531 225668 50813  818 1531(mmol/L)_.   
id                                                                           
100001        2117-09-11 09:32:00     NaN    NaN   1.9  NaN              0   
100003        2150-04-17 19:12:00     NaN    1.1   1.1  NaN              0   
100006        2108-04-08 10:58:00     NaN    NaN   4.5  4.5              0   
100007        2145-03-31 00:44:00     NaN    NaN   3.1  NaN              0   
100007        2145-04-02 14:10:00     NaN    NaN   1.9  NaN              0   

component                                                           \
status                                                               
variable_type                                                        
units                                                                
description   1531(mmol/L)_5,0 1531(mmol/L)_>30 1531(mmol/L)_>30.0   
id                                                                   
100001                       0                0                  0   
100003                       0                0                  0   
100006                       0                0                  0   
100007                       0                0                  0   
100007                       0                0                  0   

component                          ...                                     \
status                             ...                                      
variable_type                      ...                                      
units                              ...                                      
description   1531(mmol/L)_CLOTTED ... 818(mmol/L)_7.9O1B 818(mmol/L)_>30   
id                                 ...                                      
100001                           0 ...                  0               0   
100003                           0 ...                  0               0   
100006                           0 ...                  0               0   
100007                           0 ...                  0               0   
100007                           0 ...                  0               0   

component                                                              \
status                                                                  
variable_type                                                           
units                                                                   
description   818(mmol/L)_>30.0 818(mmol/L)_CLOTTED 818(mmol/L)_ERROR   
id                                                                      
100001                        0                   0                 0   
100003                        0                   0                 0   
100006                        0                   0                 0   
100007                        0                   0                 0   
100007                        0                   0                 0   

component                                                                
status                                                                   
variable_type                                              qn            
units                                                no_units            
description   818(mmol/L)_VOIDED 818(mmol/L)_no data   225668 50813 818  
id                                                                       
100001                         0                   0      NaN   NaN NaN  
100003                         0                   0      NaN   NaN NaN  
100006                         0                   0      NaN   NaN NaN  
100007                         0                   0

SAVING...


In [28]:
store = pd.HDFStore('data/mimic_data_noindex.h5')
store.select('cleaned/heart rate',where=['index<=100003']).set_index('datetime',append=True)

component                  heart rate                                        
status                          known                       unknown          
variable_type                      qn                            qn          
units                       beats/min                      no_units          
description                  211(BPM) 211(bpm) 220045(bpm)     1332 1341 1725
id     datetime                                                              
100001 2117-09-11 12:57:00        NaN      NaN       122.0      NaN  NaN  NaN
       2117-09-11 13:00:00        NaN      NaN       118.0      NaN  NaN  NaN
       2117-09-11 13:50:00        NaN      NaN       118.0      NaN  NaN  NaN
       2117-09-11 14:00:00        NaN      NaN       118.0      NaN  NaN  NaN
       2117-09-11 15:00:00        NaN      NaN       110.0      NaN  NaN  NaN
       2117-09-11 16:00:00        NaN      NaN       104.0      NaN  NaN  NaN
       2117-09-11 17:00:00        NaN      NaN       101.0      NaN  NaN  NaN
       2117-09-11 18:00:00        NaN      NaN       112.0      NaN  NaN  NaN
       2117-09-11 19:00:00        NaN      NaN       108.0      NaN  NaN  NaN
       2117-09-11 20:00:00        NaN      NaN       116.0      NaN  NaN  NaN
       2117-09-11 21:00:00        NaN      NaN       117.0      NaN  NaN  NaN
       2117-09-11 22:00:00        NaN      NaN       124.0      NaN  NaN  NaN
       2117-09-11 23:00:00        NaN      NaN       115.0      NaN  NaN  NaN
       2117-09-12 00:00:00        NaN      NaN       115.0      NaN  NaN  NaN
       2117-09-12 01:00:00        NaN      NaN       118.0      NaN  NaN  NaN
       2117-09-12 02:00:00        NaN      NaN       114.0      NaN  NaN  NaN
       2117-09-12 03:00:00        NaN      NaN       106.0      NaN  NaN  NaN
       2117-09-12 04:00:00        NaN      NaN        90.0      NaN  NaN  NaN
       2117-09-12 05:00:00        NaN      NaN        99.0      NaN  NaN  NaN
       2117-09-12 06:00:00        NaN      NaN       103.0      NaN  NaN  NaN
       2117-09-12 07:00:00        NaN      NaN       113.0      NaN  NaN  NaN
       2117-09-12 08:00:00        NaN      NaN       107.0      NaN  NaN  NaN
       2117-09-12 09:00:00        NaN      NaN       115.0      NaN  NaN  NaN
       2117-09-12 10:00:00        NaN      NaN       114.0      NaN  NaN  NaN
       2117-09-12 11:00:00        NaN      NaN       117.0      NaN  NaN  NaN
       2117-09-12 12:00:00        NaN      NaN       115.0      NaN  NaN  NaN
       2117-09-12 13:00:00        NaN      NaN       112.0      NaN  NaN  NaN
       2117-09-12 14:00:00        NaN      NaN       117.0      NaN  NaN  NaN
       2117-09-12 15:00:00        NaN      NaN       117.0      NaN  NaN  NaN
       2117-09-12 16:00:00        NaN      NaN       124.0      NaN  NaN  NaN
...                               ...      ...         ...      ...  ...  ...
100003 2150-04-18 08:00:00        NaN      NaN        75.0      NaN  NaN  NaN
       2150-04-18 09:00:00        NaN      NaN        77.0      NaN  NaN  NaN
       2150-04-18 10:00:00        NaN      NaN        82.0      NaN  NaN  NaN
       2150-04-18 11:00:00        NaN      NaN        74.0      NaN  NaN  NaN
       2150-04-18 11:18:00        NaN      NaN        76.0      NaN  NaN  NaN
       2150-04-18 12:00:00        NaN      NaN        77.0      NaN  NaN  NaN
       2150-04-18 13:00:00        NaN      NaN        75.0      NaN  NaN  NaN
       2150-04-18 14:00:00        NaN      NaN        80.0      NaN  NaN  NaN
       2150-04-18 15:00:00        NaN      NaN        80.0      NaN  NaN  NaN
       2150-04-18 16:00:00        NaN      NaN        89.0      NaN  NaN  NaN
       2150-04-18 17:00:00        NaN      NaN        82.0      NaN  NaN  NaN
       2150-04-18 18:00:00        NaN      NaN        85.0      NaN  NaN  NaN
       2150-04-18 19:00:00        NaN      NaN        88.0      NaN  NaN  NaN
       2150-04-18 20:00:00        NaN      NaN        87.0      NaN  NaN  NaN
       2150-04-18 21:0

# smart join & featurizer refactoring

In [75]:
reload(utils)
"""
HELPER METHODS
"""

def get_joined_df(components,ids,etl_manager,hdf5_fname_for_join=None):
    id_key = utils.make_list_hash(ids)
    component_key = utils.make_list_hash(components)

    joined_path = '{}/{}'.format(component_key,id_key)
    if joined_path not in store:
        paths = etl_manager.get_paths(components)
        hdf5_fname_for_join = utils.smart_join(mimic_etlM.hdf5_fname,paths,joined_path,ids,
                                                   hdf5_fname_for_join=hdf5_fname_for_join,
                                                   overwrite=False)

    return utils.read_and_reconstruct(hdf5_fname_for_join,joined_path)

In [ ]:
"""
@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@

DATA THAT IS CONSTANT FOR A GIVEN FACTORY

@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@@
"""

"""
@@ 1. DATA DICTIONARY
"""
data_dict = icu_data_defs.data_dictionary('config/data_definitions.xlsx')


"""
@@ 2. Where intermediate data will be stored
"""
hdf5_fname = 'data/test.h5'

"""
@@ 3. ETL manager if needed, and associated relevent args
"""
mimic_etlM = mimic.MimicETLManager('data/mimic_extract.h5','config/mimic_item_map.csv',data_dict)

In [5]:
"""
@@@@@@@@@@@@@@@@@@@@@@

HYPER-PARAMETERS THAT CAN (POSSIBLY) BE OPTIMIZED

@@@@@@@@@@@@@@@@@@@@@@
"""

"""
@@ 1. Info as to how we will get table
"""
hdf5_fname = mimic_extract
path = 'joined/{}'.format(utils.make_list_hash(data_dict.get_components(panel_id=12)))
data_set_info = (hdf5_fname,path)

"""
@@ 2. PRE-PROCESSING of data before features are created
"""
pre_processors = Pipeline([
                            ('drop_small_columns',transformers.remove_small_columns(threshold=100)),
                            ('drop_low_id_count',transformers.record_threshold(threshold=25)),
                            ('combine_like_columns',transformers.combine_like_cols())
                        ])

"""
@@ 3. FEATURES
"""
"""Data Specs"""
m_ureg = units.MedicalUreg()
is_summable = lambda x: m_ureg.is_volume(str(x)) or m_ureg.is_mass(str(x))

qn_not_sum = {
    column_names.VAR_TYPE : variable_type.QUANTITATIVE,
    column_names.UNITS: lambda units: not is_summable(units)
}

weight = {
    column_names.COMPONENT : data_dict.components.WEIGHT_BODY
}

intervention_summable = {
    column_names.COMPONENT : lambda comp: comp not in  [data_dict.components.WEIGHT_BODY],
    column_names.UNITS: is_summable
}

not_nominal = {
    column_names.VAR_TYPE : [variable_type.QUANTITATIVE, variable_type.ORDINAL]
}

is_nominal = {
    column_names.VAR_TYPE : variable_type.NOMINAL
}

"""Features"""
# MEAN & LAST
# For all non-summable quantities: 
# 1. ffill values
# 2. Then resample and aggregate 
# 3. Then fill with mean of means
f_qn_mean = features.Feature('MEAN','mean',
                               data_specs=[qn_not_sum,weight],
                               pre_processor=transformers.GroubyAndFFill(level=column_names.ID),
                               fillna_method=transformers.fill_mean()
                            )

f_qn_most_recent = features.Feature('LAST','last',
                                       data_specs=[qn_not_sum,weight],
                                       pre_processor=transformers.GroubyAndFFill(level=column_names.ID),
                                       fillna_method=transformers.fill_mean()
                                   )
# STD - fill NaN with 0
f_qn_std = features.Feature('STD','std',
                                data_specs=[not_nominal],
                                fillna_method=transformers.fill_zero()
                           )

# SUM - for UOP volumes and intervention volumes/masses
f_sum = features.Feature('SUM','sum',
                             data_specs=[intervention_summable],
                             fillna_method=transformers.fill_zero()
                        )

#only COUNT ordinal or quantitative data
f_count = features.Feature('COUNT','count',
                           data_specs=[not_nominal],
                           fillna_method=transformers.fill_zero())

#use SUM for nominal data (0's will be counted if we use count)
f_count_nom = features.Feature('COUNT','sum',
                             data_specs=[is_nominal],
                             fillna_method=transformers.fill_zero()
                        )

"""Lactate Label"""
# Label is lactate. just resampling; no preprocessing or filling
label = features.Feature('LABEL','mean',{
                                column_names.COMPONENT : data_dict.components.LACTATE,
                                column_names.VAR_TYPE : variable_type.QUANTITATIVE
                            })


f_list = [f_qn_mean,f_qn_most_recent,f_qn_std,f_sum,f_count,f_count_nom,label]

In [71]:
# Assume we are now getting our base data

ids = test_train_val_split(random_state=42)[0][:1000]
y=None
fit_params = None

In [66]:
"""
@@@@@@@@@@@@@@
FIT UPDATES: updates to state that need to be performed for each time the factory is FIT
1. Hyperparameters might have been adjusted
2. New set of fit_ids
@@@@@@@@@@@@@@
"""
components = features.components_for_features(f_list,data_dict,panel_id=panel_id)
etl_info = mimic_etlM.etl(components,save_steps=save_ETL_steps)

#get the joined data frame for this combination of components & ids
df_joined = get_joined_df(components,ids,mimic_etlM,hdf5_fname_target)

preprocess_key = utils.make_list_hash(map(str,pre_processors.get_params().items()))

fit_ids = ids
pre_processors.fit(df_joined,y,fit_params)

In [30]:
id_key = utils.make_list_hash(ids)
if fit: 
    


processed_path = '{}/{}/{}'.format(joined_path,preprocess_key,fit_ids_key)

In [27]:
reload(logger)



(2017-08-04 10:55:57) Smart join: n=1000, [u'glasgow coma scale eye opening', u'glasgow coma scale motor', u'blood pressure systolic', u'oxygen saturation pulse oximetry', u'lactate', u'hemoglobin', u'blood pressure mean', u'vasopressin', u'glasgow coma scale verbal', u'weight body', u'normal saline', u'norepinephrine', u'temperature body', u'blood pressure diastolic', u'heart rate', u'output urine', u'lactated ringers', u'respiratory rate']
(2017-08-04 10:55:57)>> JOINING dataframes
(2017-08-04 10:55:57)>>>> Slice & Join: 100379 --> 199940, n=1000
(2017-08-04 10:55:57)>>>>>> glasgow coma scale eye opening
(2017-08-04 10:55:58)<<<<<< --- (1.0s)
(2017-08-04 10:55:58)>>>>>> glasgow coma scale motor
(2017-08-04 10:55:59)<<<<<< --- (1.0s)
(2017-08-04 10:55:59)>>>>>> blood pressure systolic
(2017-08-04 10:56:18)<<<<<< --- (19.0s)
(2017-08-04 10:56:18)>>>>>> oxygen saturation pulse oximetry
(2017-08-04 10:56:24)<<<<<< --- (6.0s)
(2017-08-04 10:56:24)>>>>>> lactate
(2017-08-04 10:56:25)<<<<<<

<class 'pandas.io.pytables.HDFStore'>
File path: data/test.h5
File is CLOSED

In [28]:
df_joined = utils.read_and_reconstruct(hdf5_fname_target,joined_path)

In [64]:
if fit: df_processed = pre_processors.fit_transform(df_joined)
else: df_processed = pre_processors.transform(df_joined)



1709931874

In [65]:
utils.make_list_hash(map(str,pre_processors.get_params().items()))

1709931874

In [23]:
df_processed = pre_processors.fit_transform(df_joined)

(2017-08-04 10:55:22) *fit* Filter columns (remove_small_columns) (24954, 356)
(2017-08-04 10:55:22) --- (0.0s)
(2017-08-04 10:55:22) *transform* Filter columns (remove_small_columns) (24954, 356)
(2017-08-04 10:55:22) --- (0.0s)
(2017-08-04 10:55:22) *fit* Filter columns (record_threshold) (24954, 226)
(2017-08-04 10:55:22) --- (0.0s)
(2017-08-04 10:55:22) *transform* Filter columns (record_threshold) (24954, 226)
(2017-08-04 10:55:22) --- (0.0s)
(2017-08-04 10:55:22) FIT Combine like columns (24954, 223)
(2017-08-04 10:55:22)>> ('blood pressure diastolic', 'known', 'qn', 'mmHg')
(2017-08-04 10:55:22)<< --- (0.0s)
(2017-08-04 10:55:22)>> ('blood pressure diastolic', 'unknown', 'nom', 'no_units')
(2017-08-04 10:55:22)<< --- (0.0s)
(2017-08-04 10:55:22)>> ('blood pressure diastolic', 'unknown', 'qn', 'cc/min')
(2017-08-04 10:55:22)<< --- (0.0s)
(2017-08-04 10:55:22)>> ('blood pressure mean', 'known', 'qn', 'mmHg')
(2017-08-04 10:55:22)<< --- (0.0s)
(2017-08-04 10:55:22)>> ('blood pressu

In [25]:
df_processed.shape

(24954, 189)

In [ ]:
joined_path = utils.make_list_hash(components)

        if (joined_path not in store) or self.force_preprocessing:
            utils.smart_join(self.hdf5_fname_target,paths,joined_path,ids)




for component in components:
    df = ETL_manager.open_df(component,ids)
    
    

In [17]:
            logger.log('{} - {}/{}'.format(component,components.index(component)+1,len(components)),new_level=True)

            paths.append(comp_path)

            #if we have already preprocessed this component for this factory,
            #   with these ids, no need to repeat
            if (comp_path in store) and not self.force_preprocessing:
                logger.end_log_level()
                continue

            logger.log('READ DF...')
            pre_processor = self.cleaner_map[component]

            logger.log('PREPROCESS...')
            if fit: df_processed = pre_processor.fit_transform(df,y,**fit_params)
            else: df_processed = pre_processor.transform(df)

            df_processed.dropna(how='all',axis=0, inplace=True)
            df_processed.dropna(how='all',axis=1, inplace=True)
            df_processed.sort_index(axis=0, inplace=True)
            df_processed.sort_index(axis=1, inplace=True)


            logger.log('SAVE DF... {} -> {}'.format(df_processed.shape,comp_path))
            utils.deconstruct_and_write(df_processed,self.hdf5_fname_target,comp_path)
            del df,df_processed

            logger.end_log_level()


        #Join all pre-processed dataframes using pytables

        joined_path = '{}/{}'.format(root,utils.make_list_hash(components))
        if (joined_path not in store) or self.force_preprocessing:
            utils.smart_join(self.hdf5_fname_target,paths,joined_path,ids)

[139698,
 127590,
 178959,
 139276,
 196600,
 100379,
 192816,
 198838,
 190281,
 124386,
 159809,
 121194,
 145947,
 194689,
 128818,
 165644,
 174761,
 163276,
 117675,
 149359,
 154951,
 194680,
 192491,
 136852,
 118293,
 129174,
 163835,
 104843,
 176424,
 142451,
 158927,
 192791,
 107173,
 179589,
 170621,
 136080,
 113266,
 140683,
 178442,
 150285,
 127819,
 135598,
 128319,
 197642,
 198291,
 138407,
 117193,
 157669,
 169108,
 198653,
 141528,
 124229,
 190706,
 127712,
 167545,
 187720,
 181174,
 119305,
 101630,
 156216,
 162258,
 119997,
 172990,
 194924,
 123882,
 128369,
 179690,
 149465,
 174022,
 135865,
 139633,
 194386,
 193745,
 173127,
 194780,
 164261,
 151077,
 108143,
 187097,
 133220,
 136619,
 133895,
 178590,
 135268,
 145792,
 167302,
 199103,
 127765,
 125347,
 131416,
 110031,
 155893,
 190489,
 179200,
 197759,
 166310,
 199199,
 126601,
 144909,
 144148]

In [2]:
import datetime
date_times = pd.date_range(datetime.datetime(2012, 4, 5, 8, 0),
                           datetime.datetime(2012, 4, 5, 12, 0),
                           freq='1min')
tamb = np.random.sample(date_times.size) * 10.0
radiation = np.random.sample(date_times.size) * 10.0
frame = pd.DataFrame(data={'tamb': tamb, 'radiation': radiation},
                     index=date_times)

In [3]:
frame

radiation      tamb
2012-04-05 08:00:00   4.395840  2.328175
2012-04-05 08:01:00   6.973795  2.294382
2012-04-05 08:02:00   3.488426  1.777598
2012-04-05 08:03:00   0.920942  5.651255
2012-04-05 08:04:00   5.539357  5.026899
2012-04-05 08:05:00   2.626207  6.072502
2012-04-05 08:06:00   5.015794  4.095029
2012-04-05 08:07:00   1.788991  0.137189
2012-04-05 08:08:00   6.711154  5.791726
2012-04-05 08:09:00   0.787575  9.700408
2012-04-05 08:10:00   4.360875  2.878682
2012-04-05 08:11:00   6.190284  3.448838
2012-04-05 08:12:00   2.076498  6.720323
2012-04-05 08:13:00   8.741572  7.127236
2012-04-05 08:14:00   6.073471  8.908969
2012-04-05 08:15:00   9.311380  2.118503
2012-04-05 08:16:00   9.362561  7.958151
2012-04-05 08:17:00   0.846766  2.413203
2012-04-05 08:18:00   0.688412  4.189749
2012-04-05 08:19:00   5.966725  6.241028
2012-04-05 08:20:00   2.445371  3.669895
2012-04-05 08:21:00   5.894304  4.802287
2012-04-05 08:22:00   7.655295  3.944456
2012-04-05 08:23:00   9.728009  5.971919
2012-04-05 08:24:00   9.899244  2.737831
2012-04-05 08:25:00   4.091438  1.379839
2012-04-05 08:26:00   7.789243  1.581590
2012-04-05 08:27:00   5.402477  1.238280
2012-04-05 08:28:00   1.071233  1.563490
2012-04-05 08:29:00   4.361580  9.592729
...                        ...       ...
2012-04-05 11:31:00   8.790879  0.610865
2012-04-05 11:32:00   1.206108  8.588157
2012-04-05 11:33:00   6.595432  0.970133
2012-04-05 11:34:00   3.270211  4.909781
2012-04-05 11:35:00   5.496887  5.602397
2012-04-05 11:36:00   0.955139  8.984936
2012-04-05 11:37:00   2.757415  7.141076
2012-04-05 11:38:00   9.699999  1.527692
2012-04-05 11:39:00   7.672517  8.747916
2012-04-05 11:40:00   6.683253  5.607075
2012-04-05 11:41:00   5.089220  0.755786
2012-04-05 11:42:00   7.849975  2.824065
2012-04-05 11:43:00   9.994226  8.179958
2012-04-05 11:44:00   5.403646  4.864610
2012-04-05 11:45:00   9.768850  5.614152
2012-04-05 11:46:00   4.689829  9.638878
2012-04-05 11:47:00   0.185383  0.466766
2012-04-05 11:48:00   0.883917  7.018805
2012-04-05 11:49:00   8.824307  1.138941
2012-04-05 11:50:00   3.229892  7.050070
2012-04-05 11:51:00   1.745371  9.990108
2012-04-05 11:52:00   5.632322  0.032839
2012-04-05 11:53:00   0.894114  9.622544
2012-04-05 11:54:00   4.702795  5.539510
2012-04-05 11:55:00   7.413514  8.512080
2012-04-05 11:56:00   2.752037  1.620459
2012-04-05 11:57:00   8.710796  1.508803
2012-04-05 11:58:00   1.214068  9.688462
2012-04-05 11:59:00   0.830575  2.181627
2012-04-05 12:00:00   6.140628  0.195548

[241 rows x 2 columns]

In [13]:
resampled = frame.resample('1H')

In [10]:
resampled['radiation'].mean()

2012-04-05 08:00:00    4.873616
2012-04-05 09:00:00    5.030507
2012-04-05 10:00:00    5.049514
2012-04-05 11:00:00    5.187241
2012-04-05 12:00:00    6.140628
Freq: H, Name: radiation, dtype: float64

In [14]:
resampled.empty

False

In [15]:
resampled.shape

(5, 2)

In [6]:
%%timeit
frame.resample('1H').mean()

1000 loops, best of 3: 1.03 ms per loop


In [8]:
%%timeit
resampled.mean()

1000 loops, best of 3: 390 µs per loop


In [85]:
frame.resample('1H').agg({'radiation': [np.sum,np.mean], 'tamb': [np.sum,np.mean]})

tamb             radiation          
                            sum      mean         sum      mean
2012-04-05 08:00:00  326.890142  5.448169  312.025156  5.200419
2012-04-05 09:00:00  294.657090  4.910951  294.680218  4.911337
2012-04-05 10:00:00  321.037528  5.350625  320.292647  5.338211
2012-04-05 11:00:00  305.122660  5.085378  287.270681  4.787845
2012-04-05 12:00:00    8.944267  8.944267    2.622743  2.622743

In [94]:
frame.resample('1H').agg([np.mean,np.sum])

radiation                  tamb            
                         mean         sum      mean         sum
2012-04-05 08:00:00  5.200419  312.025156  5.448169  326.890142
2012-04-05 09:00:00  4.911337  294.680218  4.910951  294.657090
2012-04-05 10:00:00  5.338211  320.292647  5.350625  321.037528
2012-04-05 11:00:00  4.787845  287.270681  5.085378  305.122660
2012-04-05 12:00:00  2.622743    2.622743  8.944267    8.944267

In [115]:
%%timeit
frame2 = frame.copy()
frame2[['radiationRIGHT','tambRIGHT']] = frame
display(frame2)

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

...

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

10 loops, best of 3: 32.6 ms per loop


In [116]:
%%timeit
frame2 = frame.join(frame[['radiation','tamb']],rsuffix='RIGHT')
display(frame2)

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

...

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

radiation      tamb  radiationRIGHT  tambRIGHT
2012-04-05 08:00:00   7.348858  7.117447        7.348858   7.117447
2012-04-05 08:01:00   2.144675  2.869588        2.144675   2.869588
2012-04-05 08:02:00   3.447171  5.041280        3.447171   5.041280
2012-04-05 08:03:00   5.405834  8.389916        5.405834   8.389916
2012-04-05 08:04:00   0.532557  4.515382        0.532557   4.515382
2012-04-05 08:05:00   8.640397  1.725294        8.640397   1.725294
2012-04-05 08:06:00   9.099116  9.426689        9.099116   9.426689
2012-04-05 08:07:00   1.962370  7.585138        1.962370   7.585138
2012-04-05 08:08:00   2.328679  1.890979        2.328679   1.890979
2012-04-05 08:09:00   5.608482  5.981279        5.608482   5.981279
2012-04-05 08:10:00   1.182135  5.277603        1.182135   5.277603
2012-04-05 08:11:00   3.443349  8.077089        3.443349   8.077089
2012-04-05 08:12:00   7.909099  3.165047        7.909099   3.165047
2012-04-05 08:13:00   5.184110  4.678795        5.184110   4.678795
2012-04-05 08:14:00   8.440731  5.670249        8.440731   5.670249
2012-04-05 08:15:00   4.988947  8.076838        4.988947   8.076838
2012-04-05 08:16:00   3.600385  5.879539        3.600385   5.879539
2012-04-05 08:17:00   3.013559  4.216591        3.013559   4.216591
2012-04-05 08:18:00   9.712219  3.441322        9.712219   3.441322
2012-04-05 08:19:00   2.838503  2.336828        2.838503   2.336828
2012-04-05 08:20:00   4.336872  7.741694        4.336872   7.741694
2012-04-05 08:21:00   8.601900  5.736605        8.601900   5.736605
2012-04-05 08:22:00   6.406397  9.039525        6.406397   9.039525
2012-04-05 08:23:00   6.549001  7.424328        6.549001   7.424328
2012-04-05 08:24:00   7.810908  3.175070        7.810908   3.175070
2012-04-05 08:25:00   1.263196  1.563018        1.263196   1.563018
2012-04-05 08:26:00   4.244364  9.143346        4.244364   9.143346
2012-04-05 08:27:00   1.998993  7.987913        1.998993   7.987913
2012-04-05 08:28:00   0.576854  8.558052        0.576854   8.558052
2012-04-05 08:29:00   9.033220  8.147394        9.033220   8.147394
...                        ...       ...             ...        ...
2012-04-05 11:31:00   5.430516  3.196334        5.430516   3.196334
2012-04-05 11:32:00   1.694012  8.369825        1.694012   8.369825
2012-04-05 11:33:00   0.170623  5.165211        0.170623   5.165211
2012-04-05 11:34:00   7.147155  2.400411        7.147155   2.400411
2012-04-05 11:35:00   7.841712  4.812939        7.841712   4.812939
2012-04-05 11:36:00   1.713780  1.977316        1.713780   1.977316
2012-04-05 11:37:00   0.608180  0.171173        0.608180   0.171173
2012-04-05 11:38:00   9.817992  2.289560        9.817992   2.289560
2012-04-05 11:39:00   1.367452  7.621905        1.367452   7.621905
2012-04-05 11:40:00   9.608906  4.682637        9.608906   4.682637
2012-04-05 11:41:00   9.749052  5.173048        9.749052   5.173048
2012-04-05 11:42:00   7.023747  6.840826        7.023747   6.840826
2012-04-05 11:43:00   1.570454  6.250570        1.570454   6.250570
2012-04-05 11:44:00   8.410753  2.163854        8.410753   2.163854
2012-04-05 11:45:00   9.478709  4.713553        9.478709   4.713553
2012-04-05 11:46:00   8.527182  5.055692        8.527182   5.055692
2012-04-05 11:47:00   5.555638  7.206620        5.555638   7.206620
2012-04-05 11:48:00   6.434564  9.005622        6.434564   9.005622
2012-04-05 11:49:00   8.839207  1.092682        8.839207   1.092682
2012-04-05 11:50:00   4.822422  6.583587        4.822422   6.583587
2012-04-05 11:51:00   6.060439  8.499331        6.060439   8.499331
2012-04-05 11:52:00   6.136021  3.450341        6.136021   3.450341
2012-04-05 11:53:00   2.174187  5.334541        2.174187   5.334541
2012-04-05 11:54:00   4.683978  7.767103        4.683978   7.767103
2012-04-05 11:55:00   6.430616  2.960614        6.430616   2.960614
2012-04-05 11:56:00   9.337923  6.879604        9.337923   6.879604
2012-04-05 11:57:00   2.301911  9.998744        2.301911   9.998744
2012-04-0

10 loops, best of 3: 32.7 ms per loop


In [194]:
df = pd.DataFrame([[np.nan, 2, np.nan, 0], [3, 4, np.nan, 1],
 [np.nan, np.nan, np.nan, 5]],
columns=list('ABCD'))

In [17]:
df

A    B   C  D
0  NaN  2.0 NaN  0
1  3.0  4.0 NaN  1
2  NaN  NaN NaN  5

In [18]:
df.dropna(how='all')

A    B   C  D
0  NaN  2.0 NaN  0
1  3.0  4.0 NaN  1
2  NaN  NaN NaN  5

In [20]:
df.dropna(how='any',thresh=3)

A    B   C  D
1  3.0  4.0 NaN  1

In [197]:
df.dropna(how='any',thresh=2)

A    B   C  D
0  NaN  2.0 NaN  0
1  3.0  4.0 NaN  1

# Test: Join Function of ETL manager

In [12]:
reload(icu_data_defs)
reload(mimic)
reload(utils)

<module 'utils' from 'utils.py'>

# Test: Standalone Featurizers

In [4]:
data_dict = icu_data_defs.data_dictionary('config/data_definitions.xlsx')

In [5]:
etl_manager = mimic.MimicETLManager('data/mimic_extract.h5','config/mimic_item_map.csv',data_dict)

In [6]:
ids = test_train_val_split(random_state=42)[0][:1000]

In [18]:
df_lactate = etl_manager.open_df(data_dict.components.LACTATE,ids)

In [19]:
reload(features)
reload(transformers)

pre_processor = Pipeline([
                            ('drop_small_columns',transformers.remove_small_columns(threshold=50)),
                            ('drop_low_id_count',transformers.record_threshold(threshold=20)),
                            ('quantitative only',transformers.filter_var_type([variable_type.QUANTITATIVE])),
                            ('combine_like_columns',transformers.combine_like_cols())
                         ])


next_lac_featurizer = features.DataSpecsFeaturizer(agg_func='first',
                                                       resample_freq='2H',
                                                       data_specs={column_names.COMPONENT : data_dict.components.LACTATE},
                                                       pre_processor=pre_processor,
                                                       post_processor=transformers.Shifter(-1)
                                                  )

delta_lac_featurizer = features.DataSpecsFeaturizer(agg_func='last',
                                                       resample_freq='2H',
                                                       data_specs={column_names.COMPONENT : data_dict.components.LACTATE},
                                                       pre_processor=pre_processor,
                                                       post_processor=transformers.Delta()
                                                  )

In [20]:
next_lac_featurizer.fit_transform(df_lactate).dropna()

(2017-08-10 03:50:34) *fit* Filter columns (DataSpecFilter) (2925, 63)
(2017-08-10 03:50:34) --- (0.0s)
(2017-08-10 03:50:34) *transform* Filter columns (DataSpecFilter) (2925, 63)
(2017-08-10 03:50:34) --- (0.0s)
(2017-08-10 03:50:34) *fit* Filter columns (remove_small_columns) (2925, 63)
(2017-08-10 03:50:34) --- (0.0s)
(2017-08-10 03:50:34) *transform* Filter columns (remove_small_columns) (2925, 63)
(2017-08-10 03:50:34) --- (0.0s)
(2017-08-10 03:50:34) *fit* Filter columns (record_threshold) (2925, 4)
(2017-08-10 03:50:34) --- (0.0s)
(2017-08-10 03:50:34) *transform* Filter columns (record_threshold) (2925, 4)
(2017-08-10 03:50:34) --- (0.0s)
(2017-08-10 03:50:34) *fit* Filter columns (filter_var_type) (2925, 4)
(2017-08-10 03:50:34) --- (0.0s)
(2017-08-10 03:50:34) *transform* Filter columns (filter_var_type) (2925, 4)
(2017-08-10 03:50:34) --- (0.0s)
(2017-08-10 03:50:34) FIT Combine like columns (2925, 4)
(2017-08-10 03:50:34)>> ('lactate', 'known', 'qn', 'mmol/L')
(2017-08-10 

component                  lactate
status                       known
variable_type                   qn
units                       mmol/L
description                    all
id     datetime                   
100379 2115-10-01 04:00:00    1.00
       2115-10-01 14:00:00    1.57
       2115-10-02 14:00:00    1.10
       2115-10-03 06:00:00    1.50
       2115-10-04 02:00:00    1.40
       2115-10-07 16:00:00    4.50
       2115-10-07 18:00:00    3.10
       2115-10-07 22:00:00    2.00
       2115-10-10 14:00:00    2.10
       2115-10-13 12:00:00    1.30
       2115-10-16 10:00:00    2.40
       2115-10-16 12:00:00    5.80
101106 2130-09-14 12:00:00    6.40
       2130-09-14 14:00:00    4.90
       2130-09-14 16:00:00    2.20
101212 2120-10-15 12:00:00    1.00
101244 2162-01-26 10:00:00    2.10
       2162-01-26 16:00:00    0.90
       2162-01-26 22:00:00    1.10
       2162-01-27 00:00:00    0.90
101277 2114-10-22 08:00:00    1.10
       2114-10-22 12:00:00    2.10
       2114-10-22 18:00:00    1.50
       2114-10-22 20:00:00    3.70
       2114-10-22 22:00:00    3.30
       2114-10-23 02:00:00    2.50
       2114-10-23 06:00:00    1.30
       2114-10-23 08:00:00    2.00
101435 2156-11-10 22:00:00    2.50
101630 2141-07-26 22:00:00    1.40
...                            ...
198653 2181-01-16 22:00:00    5.50
       2181-01-17 00:00:00    5.80
       2181-01-17 02:00:00    4.90
       2181-01-17 04:00:00    4.50
       2181-01-17 14:00:00    3.80
       2181-01-18 00:00:00    2.70
       2181-01-19 00:00:00    1.40
       2181-01-19 02:00:00    1.10
198741 2196-06-23 12:00:00    1.40
198838 2139-07-16 16:00:00    1.10
199029 2110-09-28 00:00:00    0.70
199066 2106-08-24 12:00:00    2.50
       2106-08-24 16:00:00    2.30
       2106-08-24 18:00:00    2.10
       2106-08-24 22:00:00    1.20
       2106-08-25 00:00:00    2.90
199199 2192-07-31 02:00:00    2.70
       2192-08-01 04:00:00    3.60
       2192-08-01 18:00:00    4.30
       2192-08-01 20:00:00    1.40
199488 2107-09-08 18:00:00    1.70
       2107-09-09 12:00:00    1.80
       2107-09-10 22:00:00    2.60
       2107-09-11 04:00:00    2.30
       2107-09-12 04:00:00    3.30
       2107-09-14 16:00:00    1.70
       2107-09-15 04:00:00    1.30
       2107-09-15 06:00:00    1.50
199912 2198-09-19 04:00:00    1.50
199940 2108-01-11 16:00:00    1.30

[2669 rows x 1 columns]

In [21]:
delta_lac_featurizer.fit_transform(df_lactate)

(2017-08-10 03:50:44) *fit* Filter columns (DataSpecFilter) (2925, 63)
(2017-08-10 03:50:44) --- (0.0s)
(2017-08-10 03:50:44) *transform* Filter columns (DataSpecFilter) (2925, 63)
(2017-08-10 03:50:44) --- (0.0s)
(2017-08-10 03:50:44) *fit* Filter columns (remove_small_columns) (2925, 63)
(2017-08-10 03:50:44) --- (0.0s)
(2017-08-10 03:50:44) *transform* Filter columns (remove_small_columns) (2925, 63)
(2017-08-10 03:50:44) --- (0.0s)
(2017-08-10 03:50:44) *fit* Filter columns (record_threshold) (2925, 4)
(2017-08-10 03:50:44) --- (0.0s)
(2017-08-10 03:50:44) *transform* Filter columns (record_threshold) (2925, 4)
(2017-08-10 03:50:44) --- (0.0s)
(2017-08-10 03:50:44) *fit* Filter columns (filter_var_type) (2925, 4)
(2017-08-10 03:50:44) --- (0.0s)
(2017-08-10 03:50:44) *transform* Filter columns (filter_var_type) (2925, 4)
(2017-08-10 03:50:44) --- (0.0s)
(2017-08-10 03:50:44) FIT Combine like columns (2925, 4)
(2017-08-10 03:50:44)>> ('lactate', 'known', 'qn', 'mmol/L')
(2017-08-10 

component                  lactate
status                       known
variable_type                   qn
units                       mmol/L
description                    all
id     datetime                   
100379 2115-10-01 04:00:00   -1.70
       2115-10-01 14:00:00    0.57
       2115-10-02 14:00:00   -0.47
       2115-10-03 06:00:00    0.40
       2115-10-04 02:00:00   -0.10
       2115-10-07 16:00:00    3.10
       2115-10-07 18:00:00   -1.40
       2115-10-07 22:00:00   -1.10
       2115-10-10 14:00:00    0.10
       2115-10-13 12:00:00   -0.80
       2115-10-16 10:00:00    1.10
       2115-10-16 12:00:00    3.40
101106 2130-09-14 12:00:00    0.60
       2130-09-14 14:00:00   -1.50
       2130-09-14 16:00:00   -2.70
101212 2120-10-15 12:00:00   -1.20
101244 2162-01-26 10:00:00    0.60
       2162-01-26 16:00:00   -0.70
       2162-01-26 22:00:00    0.20
       2162-01-27 00:00:00   -0.20
101277 2114-10-22 08:00:00    0.20
       2114-10-22 12:00:00    1.00
       2114-10-22 18:00:00   -0.60
       2114-10-22 20:00:00    1.90
       2114-10-22 22:00:00   -0.10
       2114-10-23 02:00:00   -0.80
       2114-10-23 06:00:00   -1.20
       2114-10-23 08:00:00    0.70
101435 2156-11-10 22:00:00    0.50
101630 2141-07-26 22:00:00   -1.10
...                            ...
198653 2181-01-16 22:00:00    0.40
       2181-01-17 00:00:00   -0.50
       2181-01-17 02:00:00   -0.10
       2181-01-17 04:00:00   -0.40
       2181-01-17 14:00:00   -0.70
       2181-01-18 00:00:00   -1.10
       2181-01-19 00:00:00   -1.30
       2181-01-19 02:00:00   -0.30
198741 2196-06-23 12:00:00    0.30
198838 2139-07-16 16:00:00   -0.30
199029 2110-09-28 00:00:00   -0.40
199066 2106-08-24 12:00:00    1.80
       2106-08-24 16:00:00   -0.20
       2106-08-24 18:00:00   -0.20
       2106-08-24 22:00:00   -0.90
       2106-08-25 00:00:00    1.70
199199 2192-07-31 02:00:00   -0.20
       2192-08-01 04:00:00    0.90
       2192-08-01 18:00:00    0.70
       2192-08-01 20:00:00   -2.90
199488 2107-09-08 18:00:00    0.30
       2107-09-09 12:00:00    0.10
       2107-09-10 22:00:00    0.80
       2107-09-11 04:00:00   -0.30
       2107-09-12 04:00:00    1.00
       2107-09-14 16:00:00   -1.60
       2107-09-15 04:00:00   -0.40
       2107-09-15 06:00:00    0.20
199912 2198-09-19 04:00:00    0.00
199940 2108-01-11 16:00:00   -0.20

[2669 rows x 1 columns]

In [99]:
df_lactate.loc[100379]

component           lactate                                                    \
status                known                          unknown                    
variable_type            qn                              nom                    
units                mmol/L                         no_units                    
description            1531 225668 50813  818 1531(mmol/L)_. 1531(mmol/L)_5,0   
datetime                                                                        
2115-09-30 16:36:00     NaN    NaN  2.70  NaN              0                0   
2115-10-01 05:55:00     NaN    NaN  1.00  NaN              0                0   
2115-10-01 15:04:00     NaN    NaN  1.57  NaN              0                0   
2115-10-02 14:30:00     1.1    NaN  1.10  1.1              0                0   
2115-10-03 06:30:00     1.5    NaN  1.50  1.5              0                0   
2115-10-04 03:04:00     1.4    NaN  1.40  1.4              0                0   
2115-10-07 16:49:00     4.5    NaN  4.50  4.5              0                0   
2115-10-07 19:26:00     3.1    NaN  3.10  3.1              0                0   
2115-10-07 23:06:00     2.0    NaN  2.00  2.0              0                0   
2115-10-10 15:27:00     2.1    NaN  2.10  2.1              0                0   
2115-10-13 13:52:00     1.3    NaN  1.30  1.3              0                0   
2115-10-16 10:52:00     2.4    NaN  2.40  2.4              0                0   

component                                                                     \
status                                                                         
variable_type                                                                  
units                                                                          
description         1531(mmol/L)_>30 1531(mmol/L)_>30.0 1531(mmol/L)_CLOTTED   
datetime                                                                       
2115-09-30 16:36:00                0                  0                    0   
2115-10-01 05:55:00                0                  0                    0   
2115-10-01 15:04:00                0                  0                    0   
2115-10-02 14:30:00                0                  0                    0   
2115-10-03 06:30:00                0                  0                    0   
2115-10-04 03:04:00                0                  0                    0   
2115-10-07 16:49:00                0                  0                    0   
2115-10-07 19:26:00                0                  0                    0   
2115-10-07 23:06:00                0                  0                    0   
2115-10-10 15:27:00                0                  0                    0   
2115-10-13 13:52:00                0                  0                    0   
2115-10-16 10:52:00                0                  0                    0   

component                              ...                                     \
status                                 ...                                      
variable_type                          ...                                      
units                                  ...                                      
description         1531(mmol/L)_ERROR ... 818(mmol/L)_7.9O1B 818(mmol/L)_>30   
datetime                               ...                                      
2115-09-30 16:36:00                  0 ...                  0               0   
2115-10-01 05:55:00                  0 ...                  0               0   
2115-10-01 15:04:00                  0 ...                  0               0   
2115-10-02 14:30:00                  0 ...                  0               0   
2115-10-03 06:30:00                  0 ...                  0               0   
2115-10-04 03:04:00                  0 ...                  0               0   
2115-10-07 16:49:00                  0 ...                  0               0   
2115-10-07 19:26:00                  0 ...     

In [22]:
next_lac_featurizer.get_params()

{'agg_func': 'first',
 'data_specs': {'component': 'lactate'},
 'dropna': True,
 'fillna_transformer': do_nothing(),
 'post_processor': Shifter(shift_amount=-1),
 'post_processor__shift_amount': -1,
 'pre_processor': Pipeline(steps=[('drop_small_columns', remove_small_columns(threshold=50)), ('drop_low_id_count', record_threshold(threshold=20)), ('quantitative only', filter_var_type(var_types=['qn'])), ('combine_like_columns', combine_like_cols())]),
 'pre_processor__combine_like_columns': combine_like_cols(),
 'pre_processor__drop_low_id_count': record_threshold(threshold=20),
 'pre_processor__drop_low_id_count__threshold': 20,
 'pre_processor__drop_small_columns': remove_small_columns(threshold=50),
 'pre_processor__drop_small_columns__threshold': 50,
 'pre_processor__quantitative only': filter_var_type(var_types=['qn']),
 'pre_processor__quantitative only__var_types': ['qn'],
 'pre_processor__steps': [('drop_small_columns',
   remove_small_columns(threshold=50)),
  ('drop_low_id_cou

# Test: DataSetFactory

In [28]:
reload(features)
reload(transformers)
pre_processor = Pipeline([
                            ('drop_small_columns',transformers.remove_small_columns(threshold=50)),
                            ('drop_low_id_count',transformers.record_threshold(threshold=20)),
                            ('quantitative only',transformers.filter_var_type([variable_type.QUANTITATIVE])),
                            ('combine_like_columns',transformers.combine_like_cols())
                         ])


L_next_lac = features.DataSpecsFeaturizer(agg_func='first',
                                               resample_freq='2H',
                                               data_specs={column_names.COMPONENT : data_dict.components.LACTATE},
                                               post_processor=transformers.Shifter(-1)
                                          )

L_delta_lac = features.DataSpecsFeaturizer(agg_func='last',
                                               resample_freq='2H',
                                               data_specs={column_names.COMPONENT : data_dict.components.LACTATE},
                                               post_processor=transformers.Delta()
                                          )
F_last_lac = features.DataSpecsFeaturizer(agg_func='last',
                                                resample_freq='2H',
                                                data_specs={column_names.COMPONENT : data_dict.components.LACTATE},
                                                pre_processor=transformers.GroupbyAndFFill(level=column_names.ID)
                                          )

dsl_labels = features.DataSetFactory(
    featurizers=[
        ('LAST_LACTATE',F_last_lac),
        ('NEXT_LACTATE',L_next_lac),
        ('DELTA_LACTATE',L_delta_lac)
    ],
    resample_freq='2H',
    components=[data_dict.components.LACTATE],
    etl_manager = etl_manager,
    pre_processor=pre_processor,
)

In [29]:
df_labels = dsl_labels.fit_transform(ids)

(2017-08-10 03:53:04) *fit* Filter columns (remove_small_columns) (2925, 63)
(2017-08-10 03:53:04) --- (0.0s)
(2017-08-10 03:53:04) *transform* Filter columns (remove_small_columns) (2925, 63)
(2017-08-10 03:53:04) --- (0.0s)
(2017-08-10 03:53:04) *fit* Filter columns (record_threshold) (2925, 4)
(2017-08-10 03:53:04) --- (0.0s)
(2017-08-10 03:53:04) *transform* Filter columns (record_threshold) (2925, 4)
(2017-08-10 03:53:04) --- (0.0s)
(2017-08-10 03:53:04) *fit* Filter columns (filter_var_type) (2925, 4)
(2017-08-10 03:53:04) --- (0.0s)
(2017-08-10 03:53:04) *transform* Filter columns (filter_var_type) (2925, 4)
(2017-08-10 03:53:04) --- (0.0s)
(2017-08-10 03:53:04) FIT Combine like columns (2925, 4)
(2017-08-10 03:53:04)>> ('lactate', 'known', 'qn', 'mmol/L')
(2017-08-10 03:53:04)<< --- (0.0s)
(2017-08-10 03:53:04) --- (0.0s)
(2017-08-10 03:53:04) TRANSFORM Combine like columns (2925, 4)
(2017-08-10 03:53:04)>> ('lactate', 'known', 'qn', 'mmol/L')
(2017-08-10 03:53:04)<< --- (0.0s)

In [30]:
df_labels.describe()

feature       LAST_LACTATE NEXT_LACTATE DELTA_LACTATE
feature            lactate      lactate       lactate
component          lactate      lactate       lactate
status               known        known         known
variable_type           qn           qn            qn
units               mmol/L       mmol/L        mmol/L
description            all          all           all
count          1130.000000  1130.000000   1130.000000
mean              3.057248     3.225425      0.168177
std               3.458342     3.394432      2.567690
min               0.400000     0.400000    -21.000000
25%               1.200000     1.300000     -0.500000
50%               1.800000     2.100000      0.100000
75%               3.300000     3.500000      0.800000
max              25.100000    29.300000     21.300000

In [31]:
df_labels.head()

feature                    LAST_LACTATE NEXT_LACTATE DELTA_LACTATE
feature                         lactate      lactate       lactate
component                       lactate      lactate       lactate
status                            known        known         known
variable_type                        qn           qn            qn
units                            mmol/L       mmol/L        mmol/L
description                         all          all           all
id     datetime                                                   
100379 2115-10-07 18:00:00          4.5          3.1          -1.4
       2115-10-16 12:00:00          2.4          5.8           3.4
101106 2130-09-14 12:00:00          5.8          6.4           0.6
       2130-09-14 14:00:00          6.4          4.9          -1.5
       2130-09-14 16:00:00          4.9          2.2          -2.7

# Test: DataSetFactory with many components

In [140]:
reload(features)
reload(mimic)
reload(transformers)
reload(logger)
random_state=42
#test/train/val split
train_ids,validate_ids,test_ids = test_train_val_split(print_ids=True,random_state=random_state);

# Load Our Data Dict
data_dict = icu_data_defs.data_dictionary('config/data_definitions.xlsx')
display(data_dict.get_defs())

#init ETL Manager => mimic_extract data
etl_fname = 'data/mimic_extract.h5'
etl_manager = mimic.MimicETLManager(etl_fname,'config/mimic_item_map.csv',data_dict)

#create all features
m_ureg = units.MedicalUreg()
is_summable = lambda x: m_ureg.is_volume(str(x)) or m_ureg.is_mass(str(x))

"""
Data Specs
"""
qn_not_summable = {
    column_names.VAR_TYPE : variable_type.QUANTITATIVE,
    column_names.UNITS: lambda units: not is_summable(units)
}

summable = {
    column_names.VAR_TYPE : variable_type.QUANTITATIVE,
    column_names.COMPONENT : lambda comp: comp not in  [data_dict.components.WEIGHT_BODY],
    column_names.UNITS: is_summable
}

weight = {
    column_names.COMPONENT : data_dict.components.WEIGHT_BODY
}

not_nominal = {
    column_names.VAR_TYPE : [variable_type.QUANTITATIVE, variable_type.ORDINAL]
}

is_nominal = {
    column_names.VAR_TYPE : variable_type.NOMINAL
}

"""
FEATURES
"""

F_mean = features.DataSpecsFeaturizer(
    'mean',
    resample_freq=None,
    data_specs=[qn_not_summable,weight],
    fillna_transformer=Pipeline([
            ('ffill',transformers.GroupbyAndFFill(level=column_names.ID)),
            ('fill_mean',transformers.fill_mean())
        ])
                                     
)

F_last = features.DataSpecsFeaturizer(
    agg_func='last'
    resample_freq=None,
    data_specs=[not_nominal],
    fillna_transformer=Pipeline([
            ('ffill',transformers.GroupbyAndFFill(level=column_names.ID)),
            ('fill_mean',transformers.fill_mean())
        ])
)


F_std = features.DataSpecsFeaturizer('std',
                                      resample_freq=None,
                                      data_specs=[not_nominal],
                                      fillna_transformer=transformers.fill_zero()
                                     )

F_sum = features.DataSpecsFeaturizer('sum',
                                      resample_freq=None,
                                      data_specs=[summable],
                                      fillna_transformer=transformers.fill_zero()
                                     )

F_count = features.DataSpecsFeaturizer('count',
                                          resample_freq=None,
                                          data_specs=[not_nominal],
                                          post_processor = transformers.Replacer(0,np.nan),
                                          fillna_transformer=transformers.fill_zero()
                                      )

F_count_nom = features.DataSpecsFeaturizer('sum',
                                              resample_freq=None,
                                              data_specs=[is_nominal],
                                              fillna_transformer=transformers.fill_zero()
                                          )

"""
LABELS
"""
qn_lactate_only={
    column_names.COMPONENT : data_dict.components.LACTATE,
    column_names.VAR_TYPE : variable_type.QUANTITATIVE
}
L_next_lac = features.DataSpecsFeaturizer(agg_func='first',
                                               resample_freq=None,
                                               data_specs=qn_lactate_only,
                                               post_processor=transformers.Shifter(-1)
                                          )

L_delta_lac = features.DataSpecsFeaturizer(agg_func='last',
                                               resample_freq=None,
                                               data_specs=qn_lactate_only,
                                               post_processor=transformers.Delta()
                                           )


Train 80: 47180 > [139698, 127590, 178959, 139276, 196600] ...
Validate 80: 5898 > [112338, 107467, 158733, 144544, 115417] ...
Test 10: 5898 > [167957, 164747, 124147, 184424, 136508] ...


component       units variable_type  \
def_id                                                                          
0                                        heart rate   beats/min            qn   
1                           blood pressure systolic        mmHg            qn   
2                          blood pressure diastolic        mmHg            qn   
3                               blood pressure mean        mmHg            qn   
4                                  respiratory rate    insp/min            qn   
5                                  temperature body        degF            qn   
6                  oxygen saturation pulse oximetry     percent            qn   
7                                       weight body          kg            qn   
8                                      output urine          mL            qn   
9                                      output urine       mL/hr            qn   
10                                     output urine    mL/kg/hr            qn   
11                         glasgow coma scale motor    no_units           ord   
12                   glasgow coma scale eye opening    no_units           ord   
13                        glasgow coma scale verbal    no_units           ord   
14                                    normal saline          mL            qn   
15                                    normal saline       mL/hr            qn   
16                                 lactated ringers          mL            qn   
17                                 lactated ringers       mL/hr            qn   
18                                   norepinephrine         mcg            qn   
19                                   norepinephrine     mcg/min            qn   
20                                   norepinephrine  mcg/kg/min            qn   
21                                      vasopressin       units            qn   
22                                      vasopressin   units/min            qn   
23                                          lactate      mmol/L            qn   
24                                          lactate       mg/dL            qn   
25                                       hemoglobin        g/dL            qn   
26                           white blood cell count    x10e3/uL            qn   
27                             red blood cell count    x10e6/uL            qn   
28                                       hematocrit     percent            qn   
29                          mean corpuscular volume          fL            qn   
...                                             ...         ...           ...   
44                                    glucose serum      mmol/L            qn   
45                                    glucose serum       mg/dL            qn   
46                              glucose fingerstick      mmol/L            qn   
47                              glucose fingerstick       mg/dL            qn   
48                              calcium total serum      mmol/L            qn   
49                              calcium total serum       mg/dL            qn   
50                            calcium ionized serum      mmol/L            qn   
51                            calcium ionized serum       mg/dL            qn   
52                                  magnesium serum       mg/dL            qn   
53                                phosphorous serum       mg/dL            qn   
54                                 prothrombin time     seconds            qn   
55                      partial thromboplastin time     seconds            qn   
56                   international normalized ratio    no_units            qn   
57              partial pressure of oxygen arterial        mmHg            qn   
58      partial pressure of carbon dioxide arterial        mmHg            qn   
59                       oxygen saturation arterial     percent            qn   
60                                      pH arterial    no_units          

In [141]:
combine_like = Pipeline([
        ('drop_small_columns',transformers.remove_small_columns(threshold=50)),
        ('drop_low_id_count',transformers.record_threshold(threshold=20)),
        ('combine_like_columns',transformers.combine_like_cols())
    ])

dsf_labels = features.DataSetFactory(
    featurizers=[
        ('NEXT_LACTATE',L_next_lac),
        ('DELTA_LACTATE',L_delta_lac)
    ],
    resample_freq='2H',
    components=[data_dict.components.LACTATE],
    etl_manager = etl_manager,
    thresh = 1, #at least one of the two labels present
    pre_processor = combine_like
)

In [92]:
df_labels = dsf_labels.fit_transform(train_ids[:1000])

(2017-08-10 04:53:55)>>>> Make Feature Set. id_count=1000, #features=2
(2017-08-10 04:53:55)>>>>>> *fit* Filter columns (remove_small_columns) (2925, 63)
(2017-08-10 04:53:55)<<<<<< --- (0.0s)
(2017-08-10 04:53:55)>>>>>> *transform* Filter columns (remove_small_columns) (2925, 63)
(2017-08-10 04:53:55)<<<<<< --- (0.0s)
(2017-08-10 04:53:55)>>>>>> *fit* Filter columns (record_threshold) (2925, 4)
(2017-08-10 04:53:55)<<<<<< --- (0.0s)
(2017-08-10 04:53:55)>>>>>> *transform* Filter columns (record_threshold) (2925, 4)
(2017-08-10 04:53:55)<<<<<< --- (0.0s)
(2017-08-10 04:53:55)>>>>>> FIT Combine like columns (2925, 4)
(2017-08-10 04:53:55)>>>>>>>> ('lactate', 'known', 'qn', 'mmol/L')
(2017-08-10 04:53:55)<<<<<<<< --- (0.0s)
(2017-08-10 04:53:55)<<<<<< --- (0.0s)
(2017-08-10 04:53:55)>>>>>> TRANSFORM Combine like columns (2925, 4)
(2017-08-10 04:53:55)>>>>>>>> ('lactate', 'known', 'qn', 'mmol/L')
(2017-08-10 04:53:56)<<<<<<<< --- (1.0s)
(2017-08-10 04:53:56)<<<<<< --- (1.0s)
(2017-08-10 0

In [142]:
dsf_features = features.DataSetFactory(
    featurizers=[
        ('MEAN',F_mean),
        ('LAST',F_last),
        ('STD',F_std),
        ('SUM',F_sum),
        ('COUNT',F_count),
        ('COUNT_NOMINAL',F_count_nom),
    ],
    resample_freq='2H',
    components=data_dict.get_components(panel_id=12), # simple data
    etl_manager = etl_manager,
    thresh = 0, #at least one of the two labels present
    pre_processor = combine_like
)

In [158]:
dsf_features.resample_freq='2H'
dsf_features.components = data_dict.get_components(panel_id=12)
dsf_features.thresh = 0
dsf_features.pre_processor = combine_like
dsf_features.should_fillna = False

df_features = dsf_features.fit_transform(train_ids[:1000])

(2017-08-10 05:38:34) Make Feature Set. id_count=1000, #features=6
(2017-08-10 05:38:37)>> *fit* Filter columns (remove_small_columns) (132466, 6)
(2017-08-10 05:38:37)<< --- (0.0s)
(2017-08-10 05:38:37)>> *transform* Filter columns (remove_small_columns) (132466, 6)
(2017-08-10 05:38:37)<< --- (0.0s)
(2017-08-10 05:38:37)>> *fit* Filter columns (record_threshold) (132466, 3)
(2017-08-10 05:38:37)<< --- (0.0s)
(2017-08-10 05:38:37)>> *transform* Filter columns (record_threshold) (132466, 3)
(2017-08-10 05:38:37)<< --- (0.0s)
(2017-08-10 05:38:37)>> FIT Combine like columns (132466, 3)
(2017-08-10 05:38:37)>>>> ('heart rate', 'known', 'qn', 'beats/min')
(2017-08-10 05:38:37)<<<< --- (0.0s)
(2017-08-10 05:38:37)<< --- (0.0s)
(2017-08-10 05:38:37)>> TRANSFORM Combine like columns (132466, 3)
(2017-08-10 05:38:37)>>>> ('heart rate', 'known', 'qn', 'beats/min')
(2017-08-10 05:38:41)<<<< --- (4.0s)
(2017-08-10 05:38:41)<< --- (4.0s)
(2017-08-10 05:38:46)>> *fit* Filter columns (remove_small_

In [159]:
df_features.shape

(110141, 92)

In [161]:
df_features.dropna(how='all',axis=1).shape

(110141, 91)

In [165]:
col_na = df_features.apply(pd.isnull).sum()
row_na = df_features.apply(pd.isnull).sum(axis=1)
(df_features.shape[0] - col_na).sort_index(level='component')

feature  component                         status   variable_type  units      description
COUNT    blood pressure diastolic          known    qn             mmHg       all            43891
                                           unknown  qn             cc/min     all             2138
LAST     blood pressure diastolic          known    qn             mmHg       all            47622
                                           unknown  qn             cc/min     all            15048
MEAN     blood pressure diastolic          known    qn             mmHg       all            47622
                                           unknown  qn             cc/min     all            15048
STD      blood pressure diastolic          known    qn             mmHg       all            39006
                                           unknown  qn             cc/min     all              332
COUNT    blood pressure mean               known    qn             mmHg       all            15676
LAST     blood pres

In [157]:
row_na.value_counts().loc[df_features.shape[1]]/float(df_features.shape[0])

0.35133552014995312

In [148]:
df_features_nona = df_features.dropna(how='all')
col_na = df_features_nona.apply(pd.isnull).sum()
row_na = df_features_nona.apply(pd.isnull).sum(axis=1)
col_na.sort_values()/df_features_nona.shape[0]

feature  component                status  variable_type  units      description
MEAN     heart rate               known   qn             beats/min  all            0.000000
LAST     heart rate               known   qn             beats/min  all            0.000000
COUNT    heart rate               known   qn             beats/min  all            0.000361
MEAN     blood pressure systolic  known   qn             mmHg       all            0.014448
LAST     blood pressure systolic  known   qn             mmHg       all            0.014448
STD      heart rate               known   qn             beats/min  all            0.086148
COUNT    blood pressure systolic  known   qn             mmHg       all            0.091927
STD      blood pressure systolic  known   qn             mmHg       all            0.208236
dtype: float64

feature  component                status  variable_type  units      description
MEAN     heart rate               known   qn             beats/min  all            0.351336
LAST     heart rate               known   qn             beats/min  all            0.351336
COUNT    heart rate               known   qn             beats/min  all            0.351570
MEAN     blood pressure systolic  known   qn             mmHg       all            0.360708
LAST     blood pressure systolic  known   qn             mmHg       all            0.360708
STD      heart rate               known   qn             beats/min  all            0.407216
COUNT    blood pressure systolic  known   qn             mmHg       all            0.410965
STD      blood pressure systolic  known   qn             mmHg       all            0.486410
dtype: float64